# Logistic Regression

##### Andrew Cachia, Nov 2018

In [107]:
import pandas as pd
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.linear_model import LogisticRegression

## Data Exploration and Normalisation

In [89]:
titanic_data_csv = pd.read_csv('Titanic Dataset/train.csv')
titanic_data_csv

PassengerId  Survived  Pclass  \
0              1         0       3   
1              2         1       1   
2              3         1       3   
3              4         1       1   
4              5         0       3   
5              6         0       3   
6              7         0       1   
7              8         0       3   
8              9         1       3   
9             10         1       2   
10            11         1       3   
11            12         1       1   
12            13         0       3   
13            14         0       3   
14            15         0       3   
15            16         1       2   
16            17         0       3   
17            18         1       2   
18            19         0       3   
19            20         1       3   
20            21         0       2   
21            22         1       2   
22            23         1       3   
23            24         1       1   
24            25         0       3   
25            26         1       3   
26            27         0       3   
27            28         0       1   
28            29         1       3   
29            30         0       3   
..           ...       ...     ...   
861          862         0       2   
862          863         1       1   
863          864         0       3   
864          865         0       2   
865          866         1       2   
866          867         1       2   
867          868         0       1   
868          869         0       3   
869          870         1       3   
870          871         0       3   
871          872         1       1   
872          873         0       1   
873          874         0       3   
874          875         1       2   
875          876         1       3   
876          877         0       3   
877          878         0       3   
878          879         0       3   
879          880         1       1   
880          881         1       2   
881          882         0       3   
882          883         0       3   
883          884         0       2   
884          885         0       3   
885          886         0       3   
886          887         0       2   
887          888         1       1   
888          889         0       3   
889          890         1       1   
890          891         0       3   

                                                  Name     Sex   Age  SibSp  \
0                              Braund, Mr. Owen Harris    male  22.0      1   
1    Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                               Heikkinen, Miss. Laina  female  26.0      0   
3         Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                             Allen, Mr. William Henry    male  35.0      0   
5                                     Moran, Mr. James    male   NaN      0   
6                              McCarthy, Mr. Timothy J    male  54.0      0   
7                       Palsson, Master. Gosta Leonard    male   2.0      3   
8    Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)  female  27.0      0   
9                  Nasser, Mrs. Nicholas (Adele Achem)  female  14.0      1   
10                     Sandstrom, Miss. Marguerite Rut  female   4.0      1   
11                            Bonnell, Miss. Elizabeth  female  58.0      0   
12                      Saundercock, Mr. William Henry    male  20.0      0   
13                         Andersson, Mr. Anders Johan    male  39.0      1   
14                Vestrom, Miss. Hulda Amanda Adolfina  female  14.0      0   
15                    Hewlett, Mrs. (Mary D Kingcome)   female  55.0      0   
16                                Rice, Master. Eugene    male   2.0      4   
17                        Williams, Mr. Charles Eugene    male   NaN      0   
18   Vander Planke, Mrs. Julius (Emelia Maria Vande...  female  31.0      1   
19                             Masselmani, Mrs. Fatima  female   NaN

In [90]:
def transform_data(dataset):
    transformed_dataset = dataset[['Survived','Pclass','Sex','SibSp','Parch','Cabin']]
    
    ## Replace female and male with binary values
    transformed_dataset['Sex'].replace(['female','male'],[0,1],inplace=True)

    ## Rather than cabin numbers, determine instead whether the person had a cabin or not
    transformed_dataset.loc[~transformed_dataset['Cabin'].isnull(),'Cabin'] = 1 
    transformed_dataset.loc[transformed_dataset['Cabin'].isnull(),'Cabin'] = 0

    ## Apply mean normalization to age and fair between 1 and 0
    transformed_dataset[['Age', 'Fare']] = dataset[['Age', 'Fare']].apply(lambda x: (x - x.min()) / x.std())

    ## Split embarking into 3 binary columns
    transformed_dataset[['Embarked_C', 'Embarked_Q', 'Embarked_S']] = pd.get_dummies(dataset['Embarked'])

    transformed_dataset=transformed_dataset.dropna()
    
    return transformed_dataset


titanic_data = transform_data(titanic_data_csv)
titanic_data.head(10)

Survived  Pclass  Sex  SibSp  Parch  Cabin       Age      Fare  \
0          0       3    1      1      0      0  1.485561  0.145895   
1          1       1    0      1      0      1  2.586997  1.434461   
2          1       3    0      0      0      0  1.760920  0.159478   
3          1       1    0      1      0      1  2.380477  1.068552   
4          0       3    1      0      0      0  2.380477  0.161993   
6          0       1    1      0      0      1  3.688432  1.043649   
7          0       3    1      3      1      0  0.108767  0.424100   
8          1       3    0      0      2      0  1.829760  0.224040   
9          1       2    0      1      0      0  0.934843  0.605126   
10         1       3    0      1      1      1  0.246446  0.336061   

    Embarked_C  Embarked_Q  Embarked_S  
0            0           0           1  
1            1           0           0  
2            0           0           1  
3            0           0           1  
4            0           0           1  
6            0           0           1  
7            0           0           1  
8            0           0           1  
9            1           0           0  
10           0           0           1

## Gradient Descent Algorithm

In [91]:
Y = pd.to_numeric(titanic_data['Survived'])
X = titanic_data.loc[:, titanic_data.columns != 'Survived']
Q = np.zeros(X.shape[1])

alpha = 0.1
error_threshold = 0.5

In [92]:
def sigmoid(X, Q):
    Z = np.dot(X, Q)
    return 1 / (1 + np.exp(-Z))

$$ -ylog(\hat y) - ((1-y)log(1-\hat y)) $$

In [93]:
def cost_function(actual_y, predicted_y):
    return -np.dot(actual_y,np.log(predicted_y)) - (np.dot((1-actual_y),np.log(1-predicted_y))).mean()

$$ (\hat y - y)x $$

In [94]:
def gradient(predicted_y, actual_y, x):
    return np.dot((predicted_y - actual_y),x) / actual_y.shape[0]

In [95]:
count=0

while count < 30000:
    count += 1
    Predicted = sigmoid(X,Q)
    cost = cost_function(Y,Predicted)
    error = gradient(Predicted, Y, X)
    Q -= alpha * error
    print(count)
    print(cost)
    print(error)


1
494.9070869198009
[ 0.35784314  0.18697479  0.05602241  0.00140056 -0.04551821  0.22703368
 -0.07464784 -0.01960784  0.00840336  0.10644258]
2
479.9201899310421
[ 0.2721969   0.16237223  0.0382028  -0.01278514 -0.05197282  0.15322601
 -0.09260832 -0.02451001  0.00688093  0.07747352]
3
470.68206511517695
[ 0.21079483  0.14470306  0.02583781 -0.02232307 -0.05604985  0.10159504
 -0.10367891 -0.02773862  0.00578194  0.05682989]
4
464.44807781155464
[ 0.16655612  0.13194007  0.01730666 -0.02860917 -0.05847441  0.06557963
 -0.10996371 -0.0297974   0.00498303  0.0420708 ]
5
459.83344139314227
[ 0.13433105  0.12260771  0.01144231 -0.03264316 -0.05975995  0.04043404
 -0.11296003 -0.03104565  0.00439433  0.03142532]
6
456.1356197941213
[ 0.11053832  0.11567961  0.00743608 -0.03511527 -0.06026137  0.02286778
 -0.1137072  -0.03173272  0.00395338  0.02366305]
7
452.991918526145
[ 0.09271045  0.11044859  0.00473111 -0.03649994 -0.06022389  0.01061695
 -0.11292653 -0.03203127  0.00361712  0.0179364

185
364.267499492313
[-0.00797901  0.03895468  0.00504029  0.00510285 -0.01742545  0.00259762
 -0.00368235 -0.01163689  0.00068694 -0.00990741]
186
364.1113709715211
[-0.00793916  0.03879835  0.00500637  0.005109   -0.01738195  0.00258777
 -0.00363542 -0.01161438  0.00068445 -0.00990412]
187
363.9563514776263
[-0.00789939  0.03864282  0.00497267  0.00511472 -0.01733871  0.00257797
 -0.00358908 -0.01159205  0.00068196 -0.00990075]
188
363.80243101443637
[-0.0078597   0.03848807  0.00493918  0.00512001 -0.01729573  0.00256822
 -0.00354329 -0.0115699   0.00067947 -0.00989732]
189
363.6495996976757
[-0.00782009  0.03833411  0.00490591  0.00512488 -0.017253    0.00255852
 -0.00349807 -0.01154794  0.00067699 -0.00989381]
190
363.49784775328305
[-0.00778058  0.03818093  0.00487286  0.00512934 -0.01721051  0.00254888
 -0.00345339 -0.01152615  0.00067451 -0.00989023]
191
363.3471655157497
[-0.00774115  0.03802852  0.00484003  0.0051334  -0.01716827  0.00253929
 -0.00340925 -0.01150454  0.000672

  0.00057765 -0.00900673  0.0001406  -0.00866983]
394
346.22129519265167
[-0.00254002  0.01807939  0.00151036  0.00328226 -0.01125573  0.00159147
  0.00058607 -0.0089992   0.00013783 -0.00866343]
395
346.1762257536056
[-0.00252554  0.01801841  0.00150383  0.00327154 -0.01123435  0.00158967
  0.00059443 -0.0089917   0.00013506 -0.00865704]
396
346.1313764292097
[-0.00251113  0.01795767  0.00149735  0.00326084 -0.01121301  0.00158787
  0.00060274 -0.00898422  0.00013229 -0.00865065]
397
346.08674574438976
[-0.00249679  0.01789719  0.00149091  0.00325017 -0.01119173  0.00158609
  0.00061099 -0.00897676  0.00012952 -0.00864426]
398
346.04233223575045
[-0.00248253  0.01783695  0.00148452  0.00323952 -0.0111705   0.00158432
  0.00061919 -0.00896933  0.00012674 -0.00863789]
399
345.9981344514705
[-0.00246833  0.01777696  0.00147818  0.0032289  -0.01114931  0.00158256
  0.00062733 -0.00896192  0.00012397 -0.00863151]
400
345.9541509511994
[-0.0024542   0.01771721  0.00147189  0.0032183  -0.011

600
340.08795025496397
[-0.00062112  0.00945714  0.00076949  0.00160979 -0.00768956  0.00134165
  0.00152281 -0.00780271 -0.00042417 -0.00747755]
601
340.06845778075547
[-0.00061538  0.00942951  0.00076757  0.00160408 -0.00767554  0.00134069
  0.00152475 -0.00779806 -0.00042679 -0.00747249]
602
340.0490300701349
[-0.00060966  0.00940199  0.00076566  0.00159839 -0.00766155  0.00133973
  0.00152667 -0.00779342 -0.00042941 -0.00746744]
603
340.02966678705593
[-0.00060397  0.00937456  0.00076376  0.00159272 -0.00764758  0.00133877
  0.00152857 -0.00778878 -0.00043203 -0.00746239]
604
340.0103675976378
[-0.0005983   0.00934723  0.00076187  0.00158707 -0.00763364  0.00133782
  0.00153046 -0.00778415 -0.00043465 -0.00745735]
605
339.9911321701493
[-0.00059265  0.00932     0.00075999  0.00158144 -0.00761973  0.00133686
  0.00153233 -0.00777953 -0.00043727 -0.00745232]
606
339.97196017499255
[-0.00058703  0.00929286  0.00075812  0.00157582 -0.00760584  0.0013359
  0.00153419 -0.00777491 -0.0004

  0.00165887 -0.00694556 -0.00094545 -0.00653771]
814
336.9908705484139
[ 0.00021583  0.00528281  0.00049227  0.00074865 -0.00518922  0.00114552
  0.00165858 -0.00694203 -0.00094771 -0.00653389]
815
336.9800573949204
[ 0.00021839  0.0052695   0.0004914   0.00074597 -0.00517954  0.00114464
  0.00165829 -0.00693851 -0.00094997 -0.00653008]
816
336.9692686291951
[ 0.00022094  0.00525623  0.00049053  0.0007433  -0.00516988  0.00114376
  0.00165799 -0.006935   -0.00095222 -0.00652627]
817
336.9585041542316
[ 0.00022348  0.00524301  0.00048966  0.00074063 -0.00516024  0.00114288
  0.00165768 -0.00693149 -0.00095447 -0.00652247]
818
336.9477638735237
[ 0.00022602  0.00522983  0.00048879  0.00073798 -0.00515061  0.001142
  0.00165737 -0.00692798 -0.00095672 -0.00651867]
819
336.93704769106307
[ 0.00022854  0.00521669  0.00048793  0.00073534 -0.005141    0.00114112
  0.00165706 -0.00692448 -0.00095897 -0.00651487]
820
336.9263555113357
[ 0.00023106  0.00520359  0.00048706  0.0007327  -0.0051314

...

29201
319.3170488617557
[ 4.10576857e-05  1.42324425e-05  4.99508319e-06 -3.04648832e-07
  3.41852993e-05  1.56116794e-05  9.29007074e-06 -1.51234880e-04
 -1.91614226e-04 -1.48791169e-04]
29202
319.31704278316363
[ 4.10533662e-05  1.42309909e-05  4.99456671e-06 -3.04613604e-07
  3.41816937e-05  1.56100527e-05  9.28907730e-06 -1.51219022e-04
 -1.91594045e-04 -1.48775561e-04]
29203
319.31703670584875
[ 4.10490471e-05  1.42295393e-05  4.99405028e-06 -3.04578380e-07
  3.41780885e-05  1.56084261e-05  9.28808397e-06 -1.51203166e-04
 -1.91573867e-04 -1.48759954e-04]
29204
319.31703062981103
[ 4.10447285e-05  1.42280879e-05  4.99353391e-06 -3.04543161e-07
  3.41744837e-05  1.56067998e-05  9.28709075e-06 -1.51187312e-04
 -1.91553690e-04 -1.48744349e-04]
29205
319.31702455505024
[ 4.10404104e-05  1.42266367e-05  4.99301759e-06 -3.04507946e-07
  3.41708793e-05  1.56051736e-05  9.28609765e-06 -1.51171459e-04
 -1.91533516e-04 -1.48728746e-04]
29206
319.3170184815659
[ 4.10360927e-05  1.42251856e-05

319.31593993786214
[ 4.02621553e-05  1.39649232e-05  4.89993058e-06 -2.98172267e-07
  3.35212846e-05  1.53120293e-05  9.10716603e-06 -1.48314109e-04
 -1.87897600e-04 -1.45916422e-04]
29388
319.3159340922643
[ 4.02579209e-05  1.39634984e-05  4.89942393e-06 -2.98137856e-07
  3.35177504e-05  1.53104341e-05  9.10619279e-06 -1.48298562e-04
 -1.87877818e-04 -1.45901120e-04]
29389
319.3159282478944
[ 4.02536869e-05  1.39620737e-05  4.89891734e-06 -2.98103448e-07
  3.35142166e-05  1.53088390e-05  9.10521965e-06 -1.48283016e-04
 -1.87858038e-04 -1.45885819e-04]
29390
319.3159224047523
[ 4.02494534e-05  1.39606492e-05  4.89841080e-06 -2.98069045e-07
  3.35106831e-05  1.53072440e-05  9.10424662e-06 -1.48267472e-04
 -1.87838260e-04 -1.45870520e-04]
29391
319.31591656283763
[ 4.02452204e-05  1.39592248e-05  4.89790431e-06 -2.98034647e-07
  3.35071500e-05  1.53056493e-05  9.10327370e-06 -1.48251929e-04
 -1.87818484e-04 -1.45855223e-04]
29392
319.31591072215025
[ 4.02409878e-05  1.39578006e-05  4.897

 -1.84041161e-04 -1.42933050e-04]
29585
319.3148061315485
[ 3.94325141e-05  1.36855868e-05  4.80062899e-06 -2.91442445e-07
  3.28288659e-05  1.49994105e-05  8.91654178e-06 -1.45267698e-04
 -1.84021793e-04 -1.42918065e-04]
29586
319.3148005240963
[ 3.94283684e-05  1.36841901e-05  4.80013261e-06 -2.91408879e-07
  3.28254061e-05  1.49978481e-05  8.91558955e-06 -1.45252474e-04
 -1.84002426e-04 -1.42903081e-04]
29587
319.3147949178217
[ 3.94242232e-05  1.36827935e-05  4.79963628e-06 -2.91375317e-07
  3.28219466e-05  1.49962858e-05  8.91463743e-06 -1.45237252e-04
 -1.83983061e-04 -1.42888099e-04]
29588
319.31478931272454
[ 3.94200784e-05  1.36813971e-05  4.79914000e-06 -2.91341760e-07
  3.28184876e-05  1.49947236e-05  8.91368541e-06 -1.45222031e-04
 -1.83963698e-04 -1.42873119e-04]
29589
319.3147837088044
[ 3.94159340e-05  1.36800008e-05  4.79864377e-06 -2.91308206e-07
  3.28150289e-05  1.49931617e-05  8.91273350e-06 -1.45206812e-04
 -1.83944338e-04 -1.42858140e-04]
29590
319.3147781060611
[

29798
319.31363794070063
[ 3.85594106e-05  1.33912351e-05  4.69604924e-06 -2.84387000e-07
  3.21002484e-05  1.46702820e-05  8.71606693e-06 -1.42061250e-04
 -1.79943143e-04 -1.39762250e-04]
29799
319.31363257853366
[ 3.85553583e-05  1.33898680e-05  4.69556366e-06 -2.84354317e-07
  3.20968668e-05  1.46687540e-05  8.71513678e-06 -1.42046367e-04
 -1.79924213e-04 -1.39747601e-04]
29800
319.31362721749235
[ 3.85513063e-05  1.33885011e-05  4.69507814e-06 -2.84321639e-07
  3.20934855e-05  1.46672263e-05  8.71420672e-06 -1.42031485e-04
 -1.79905284e-04 -1.39732955e-04]
29801
319.31362185757655
[ 3.85472548e-05  1.33871342e-05  4.69459266e-06 -2.84288964e-07
  3.20901046e-05  1.46656987e-05  8.71327678e-06 -1.42016605e-04
 -1.79886359e-04 -1.39718310e-04]
29802
319.31361649878596
[ 3.85432037e-05  1.33857675e-05  4.69410724e-06 -2.84256294e-07
  3.20867241e-05  1.46641712e-05  8.71234693e-06 -1.42001726e-04
 -1.79867435e-04 -1.39703666e-04]
29803
319.31361114112036
[ 3.85391530e-05  1.33844010e-

29987
319.31264422919855
[ 3.78011460e-05  1.31352816e-05  4.60516151e-06 -2.78281942e-07
  3.14675277e-05  1.43843332e-05  8.54207319e-06 -1.39276175e-04
 -1.76401119e-04 -1.37021198e-04]
29988
319.3126390756138
[ 3.77971745e-05  1.31339402e-05  4.60468533e-06 -2.78250022e-07
  3.14642140e-05  1.43828353e-05  8.54116218e-06 -1.39261587e-04
 -1.76382568e-04 -1.37006841e-04]
29989
319.3126339231107
[ 3.77932035e-05  1.31325990e-05  4.60420920e-06 -2.78218105e-07
  3.14609006e-05  1.43813375e-05  8.54025126e-06 -1.39247000e-04
 -1.76364019e-04 -1.36992485e-04]
29990
319.312628771689
[ 3.77892330e-05  1.31312580e-05  4.60373312e-06 -2.78186193e-07
  3.14575876e-05  1.43798399e-05  8.53934044e-06 -1.39232416e-04
 -1.76345472e-04 -1.36978131e-04]
29991
319.3126236213484
[ 3.77852628e-05  1.31299170e-05  4.60325709e-06 -2.78154284e-07
  3.14542749e-05  1.43783424e-05  8.53842972e-06 -1.39217833e-04
 -1.76326927e-04 -1.36963779e-04]
29992
319.3126184720886
[ 3.77812931e-05  1.31285762e-05  4.

In [116]:
## Resulting parameter weights after training
Q

array([-0.78433948, -2.62045702, -0.34068938, -0.08215087,  0.78802917,
       -0.52375614,  0.10166118,  4.22821864,  3.3544208 ,  3.86370876])

### Comparing with sklearn toolkit implementation

In [117]:
model = LogisticRegression(C=1e20)

model.fit(X, Y)

model.coef_

/home/andrew/anaconda3/envs/ics5110/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)


array([[-1.01353688, -2.64606728, -0.36291884, -0.06678579,  0.5444916 ,
        -0.63375472,  0.04116372, -4.1201468 , -4.94374704, -4.49740869]])

## Testing

In [119]:
titanic_test_data_csv = pd.read_csv('Titanic Dataset/train.csv')
titanic_test_data = transform_data(titanic_test_data_csv)

test_parameters = titanic_test_data.loc[:, titanic_data.columns != 'Survived']
expected = titanic_test_data['Survived']

actual = sigmoid(test_parameters,Q)

result = pd.DataFrame(np.vstack((expected.values, actual))).T

result.head(20)

0         1
0   0.0  0.098527
1   1.0  0.935962
2   1.0  0.646710
3   1.0  0.915950
4   0.0  0.087857
5   0.0  0.359209
6   0.0  0.097278
7   1.0  0.601284
8   1.0  0.868840
9   1.0  0.855816
10  1.0  0.863616
11  0.0  0.141941
12  0.0  0.039611
13  0.0  0.738296
14  1.0  0.589008
15  0.0  0.044730
16  0.0  0.526040
17  0.0  0.179605
18  1.0  0.327054
19  1.0  0.620611

### Statistics

In [120]:
actual[actual >= 0.5] = 1
actual[actual < 0.5] = 0

accuracy = np.sum(expected == actual) / actual.shape[0] * 100
conf_matrix = confusion_matrix(expected, actual)
precision = conf_matrix[0,0] / (conf_matrix[0,0] + conf_matrix[0,1]) * 100

print("Accuracy: {0:.2f}%".format(accuracy))
print("Precision: {0:.2f}%".format(precision))

Accuracy: 79.69%
Precision: 85.38%


In [121]:
scikit_predicted = model.predict(test_parameters)

scikit_predicted[scikit_predicted >= 0.5] = 1
scikit_predicted[scikit_predicted < 0.5] = 0

accuracy = np.sum(expected == scikit_predicted) / scikit_predicted.shape[0] * 100
conf_matrix = confusion_matrix(expected, scikit_predicted)
precision = conf_matrix[0,0] / (conf_matrix[0,0] + conf_matrix[0,1]) * 100

print("Scikit Accuracy: {0:.2f}%".format(accuracy))
print("Scikit Precision: {0:.2f}%".format(precision))

Scikit Accuracy: 80.25%
Scikit Precision: 85.61%
